In [1]:
import open3d as o3d
import trimesh
import numpy as np

# Read point cloud from file
pcd = o3d.io.read_point_cloud("base_dilated.ply")

# Estimate normals for the point cloud
pcd.estimate_normals()

# Estimate radius for rolling ball
distances = pcd.compute_nearest_neighbor_distance()
avg_dist = np.mean(distances)
radius = 1.5 * avg_dist

# Create a mesh from the point cloud using the ball pivoting algorithm
mesh = o3d.geometry.TriangleMesh.create_from_point_cloud_ball_pivoting(
           pcd,
           o3d.utility.DoubleVector([radius, radius * 2]))

# Create the triangular mesh with the vertices and faces from Open3D mesh
tri_mesh = trimesh.Trimesh(np.asarray(mesh.vertices), np.asarray(mesh.triangles),
                          vertex_normals=np.asarray(mesh.vertex_normals))

# Check if the mesh is convex (Optional, depending on your needs)
is_convex = trimesh.convex.is_convex(tri_mesh)
print(f"Is the mesh convex? {is_convex}")

# Export the triangular mesh to a new PLY file
tri_mesh.export('output_mesh.ply')

Is the mesh convex? False


b'ply\nformat binary_little_endian 1.0\ncomment https://github.com/mikedh/trimesh\nelement vertex 30991\nproperty float x\nproperty float y\nproperty float z\nproperty float nx\nproperty float ny\nproperty float nz\nelement face 58521\nproperty list uchar int vertex_indices\nend_header\n\xbd\xff\x0f=\x08\x00f?\xa7w\xf1<\xc7\x1d\x83>Bvu\xbf\xd0F\xfb\xbdz\xff\x1f=\x08\x00f?\xbd6\x1b=\xedu\x1f>\xff9x\xbf;\x18A\xbeC\x000=\x08\x00f?*\xca%={\x14\xd4=\x8foz\xbfy\xf67\xbe\x00\x00@=\x08\x00f?E\x10\'=\t\xd2\xf7<\xe3\x85y\xbfo\xc7b\xbe\xbd\xffO=\x08\x00f?R\x9c#=\xe7\x1d\x1e\xbdF\xf6y\xbf\x93\x86Y\xbe\x86\x00`=\x08\x00f?\xdd#\x1b=U\x98\xd8\xbd\xb1\xb5y\xbf\x00\xe9E\xbeC\x00p=\x08\x00f?\x83\xdc\x05=\xdf\xce\x10\xbe\x9f\x98z\xbf\xe4\x19\x17\xbe\x00\x00\x80=\x08\x00f?\xf9\x86\xc2<\xe4\x8fF\xbe\xfc\x82y\xbf\xd1}\xe4\xbd\x0c\x01\xc0<\xfc\xffd?\xf8\x1c\xd8<;\x8c\xd2>\xf0\x83g\xbf\x92\xca\xe9\xbd\x86\x00\xe0<\xfc\xffd?\x0f\x0c =\xe6\xd1\xbe>\x88\x8fh\xbf)\xd8A\xbe\x00\x00\x00=\xfc\xffd?\xde\xcb==1\xe7\x9

In [2]:
import open3d as o3d
import numpy as np
from scipy.spatial import cKDTree

def inpaint_point_cloud(pcd, radius):
    # Compute kdtree for fast nearest neighbor search
    kdtree = cKDTree(np.asarray(pcd.points))

    # Identify boundary points
    boundary_points = []
    for i, point in enumerate(pcd.points):
        indices = kdtree.query_ball_point(point, radius)
        if len(indices) < 20:  # Adjust the threshold based on your requirement
            boundary_points.append(i)

    # Interpolate boundary points
    for i in boundary_points:
        point = pcd.points[i]
        indices = kdtree.query_ball_point(point, radius)
        neighbors = np.asarray(pcd.points)[indices]
        interpolated_point = np.mean(neighbors, axis=0)  # Simple averaging for interpolation
        pcd.points[i] = interpolated_point

    return pcd

# Read point cloud
pcd = o3d.io.read_point_cloud("base_dilated.ply")

# Inpaint the point cloud
radius = 0.1  # Adjust the radius based on your point cloud density
inpaint_point_cloud(pcd, radius)

# Save the inpainted point cloud
o3d.io.write_point_cloud("inpaint_pointcloud.ply", pcd)

True